In [1]:
%pwd

'/home/acr/Documents/Projeto Sistemas Mecatrónicos/Demand Response'

In [2]:
import gym
import Antonio_FlexEnv as flex

import Antonio_auxfunctions as fun

import stable_baselines3

from stable_baselines3 import DQN, A2C
from stable_baselines3.a2c.policies import MlpPolicy

from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.env_checker import check_env

from stable_baselines3 import SAC
from stable_baselines3 import DDPG

from stable_baselines3 import PPO
from stable_baselines3.common.env_util import make_vec_env

from stable_baselines3.ddpg.policies import MlpPolicy


import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt
import numpy.random as rnd
import time
import random as rnd


# Data and Environment preparation

In [3]:
#Data
cwd=os.getcwd()
datafolder=cwd + '/Data'

#impor the data csv
env_data=pd.read_csv(datafolder + '/env_data.csv', header = None)

#make and check the environment
# Select the number of timesteps to consider
# timesteps=141
timesteps=47

#Create environment. Based on the aux functions code.
env=fun.make_env(env_data, load_num=4, timestep=timesteps, soc_max=2, eta=0.95, charge_lim=3)

In [4]:
env.observation_space

Box([   0.    0.    0.    0.    0.    0. -100.    0. -100.], [ 47.  10.  10.   2.   2.   1. 100.   1. 100.], (9,), float32)

In [5]:
env.observation_space.high[3]

2.0

In [6]:
env.action_space

Discrete(15)

In [7]:
# help(env.action_space)

In [8]:
# charge_steps

In [9]:
data=env_data
load_num=4
timestep=timesteps

env_data
env_data1=data.to_numpy()
load=env_data1[0:timestep,load_num]
gen=abs(env_data1[0:timestep,1])
data1=np.vstack((0.5*gen,6*load)).T

In [10]:
env_data

0    1      2      3      4      5      6      7   \
0     2017-01-01 00:00:00  0.0  0.023  0.489  0.033  0.039  0.082  0.326   
1     2017-01-01 00:30:00 -0.0  0.046  0.490  0.075  0.040  0.099  0.224   
2     2017-01-01 01:00:00 -0.0  0.020  0.493  0.031  0.086  0.088  0.132   
3     2017-01-01 01:30:00 -0.0  0.042  0.494  0.084  0.133  0.104  0.203   
4     2017-01-01 02:00:00 -0.0  0.032  0.503  0.095  0.064  0.077  0.063   
...                   ...  ...    ...    ...    ...    ...    ...    ...   
8683  2017-06-30 21:30:00 -0.0  0.085  0.123  0.092  0.131  0.072  0.227   
8684  2017-06-30 22:00:00 -0.0  0.025  0.116  0.129  0.133  0.030  0.199   
8685  2017-06-30 22:30:00 -0.0  0.059  0.111  0.089  0.096  0.059  0.192   
8686  2017-06-30 23:00:00 -0.0  0.024  0.094  0.093  0.067  0.083  0.193   
8687  2017-06-30 23:30:00 -0.0  0.056  0.116  0.078  0.103  0.564  0.165   

         8      9      10     11  
0     0.786  0.016  0.238  0.084  
1     0.759  0.013  0.442  0.082  
2     0.771  0.008  0.395  0.125  
3     0.727  0.016  0.283  0.118  
4     0.711  0.033  0.450  0.159  
...     ...    ...    ...    ...  
8683  0.344  0.007  0.190  0.171  
8684  0.332  0.041  0.144  0.174  
8685  0.276  0.035  0.407  0.211  
8686  0.283  0.090  0.169  0.178  
8687  0.295  0.099  0.180  0.257  

[8688 rows x 12 columns]

In [11]:
env_data[4]

0       0.033
1       0.075
2       0.031
3       0.084
4       0.095
        ...  
8683    0.092
8684    0.129
8685    0.089
8686    0.093
8687    0.078
Name: 4, Length: 8688, dtype: float64

In [12]:
env_data1.shape # 1a coluna é a data, 2a é a geração, 3a a 12a são colunas de gastos energéticos

(8688, 12)

In [13]:
env_data1

array([['2017-01-01 00:00:00', 0.0, 0.023, ..., 0.016, 0.238, 0.084],
       ['2017-01-01 00:30:00', -0.0, 0.046, ..., 0.013, 0.442, 0.082],
       ['2017-01-01 01:00:00', -0.0, 0.02, ..., 0.008, 0.395, 0.125],
       ...,
       ['2017-06-30 22:30:00', -0.0, 0.059, ..., 0.035, 0.407, 0.211],
       ['2017-06-30 23:00:00', -0.0, 0.024, ..., 0.09, 0.169, 0.178],
       ['2017-06-30 23:30:00', -0.0, 0.056, ..., 0.099, 0.18, 0.257]],
      dtype=object)

In [14]:
load.shape

(47,)

In [15]:
env_data1[0:timestep,4] # É só um dia de dados 

array([0.033, 0.075, 0.031, 0.084, 0.095, 0.106, 0.099, 0.042, 0.071,
       0.028, 0.076, 0.037, 0.064, 0.054, 0.097, 0.12, 0.074, 0.079,
       0.034, 0.068, 0.05, 0.053, 0.062, 0.037, 0.121, 0.073, 0.12, 0.048,
       0.057, 0.06, 0.042, 0.075, 0.025, 0.077, 0.088, 0.111, 0.098,
       0.053, 0.065, 0.036, 0.075, 0.026, 0.073, 0.042, 0.098, 0.107,
       0.09], dtype=object)

In [16]:
data1 # # Duas colunas, a primeira retrata a geração, a segunda representa os gastos energéticos da casa 

array([[0.0, 0.198],
       [0.0, 0.44999999999999996],
       [0.0, 0.186],
       [0.0, 0.504],
       [0.0, 0.5700000000000001],
       [0.0, 0.636],
       [0.0, 0.5940000000000001],
       [0.0, 0.252],
       [0.0, 0.42599999999999993],
       [0.0, 0.168],
       [0.0, 0.45599999999999996],
       [0.0, 0.22199999999999998],
       [0.0, 0.384],
       [0.0, 0.324],
       [0.0, 0.5820000000000001],
       [0.0, 0.72],
       [0.036000000000000004, 0.44399999999999995],
       [0.15000000000000002, 0.474],
       [0.34500000000000003, 0.20400000000000001],
       [0.5925, 0.40800000000000003],
       [0.8939999999999999, 0.30000000000000004],
       [1.0605, 0.318],
       [1.137, 0.372],
       [1.257, 0.22199999999999998],
       [1.653, 0.726],
       [1.4144999999999999, 0.43799999999999994],
       [1.0035, 0.72],
       [1.2494999999999998, 0.28800000000000003],
       [0.9135, 0.342],
       [0.3405, 0.36],
       [0.42299999999999993, 0.252],
       [0.4575, 0.4499999999

In [17]:
data1.shape

(47, 2)

In [18]:
np.vstack((1.5*gen,6*load))

array([[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,
        0.0, 0.0, 0.0, 0.036000000000000004, 0.15000000000000002,
        0.34500000000000003, 0.5925, 0.8939999999999999, 1.0605, 1.137,
        1.257, 1.653, 1.4144999999999999, 1.0035, 1.2494999999999998,
        0.9135, 0.3405, 0.42299999999999993, 0.4575, 0.22799999999999998,
        0.08700000000000001, 0.013499999999999998, 0.0, 0.0, 0.0, 0.0,
        0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
       [0.198, 0.44999999999999996, 0.186, 0.504, 0.5700000000000001,
        0.636, 0.5940000000000001, 0.252, 0.42599999999999993, 0.168,
        0.45599999999999996, 0.22199999999999998, 0.384, 0.324,
        0.5820000000000001, 0.72, 0.44399999999999995, 0.474,
        0.20400000000000001, 0.40800000000000003, 0.30000000000000004,
        0.318, 0.372, 0.22199999999999998, 0.726, 0.43799999999999994,
        0.72, 0.28800000000000003, 0.342, 0.36, 0.252,
        0.44999999999999996, 0.15000000000000002, 0.4619999999

# Generation values
Data analysis to understand the data of the PV's

In [19]:
# Values of generation
env_data[1].value_counts()

0.000    4107
1.764     105
0.003      43
0.001      36
0.002      35
         ... 
0.866       1
1.330       1
1.730       1
1.740       1
0.804       1
Name: 1, Length: 1570, dtype: int64

In [20]:
env_data[env_data[1] ==1.764][0] # Dias e horas para as quais a geração de energia é maior

1849    2017-02-08 12:30:00
1850    2017-02-08 13:00:00
2426    2017-02-20 13:00:00
3002    2017-03-04 13:00:00
3145    2017-03-07 12:30:00
               ...         
6648    2017-05-19 12:00:00
6649    2017-05-19 12:30:00
6695    2017-05-20 11:30:00
6696    2017-05-20 12:00:00
6697    2017-05-20 12:30:00
Name: 0, Length: 105, dtype: object

In [21]:
df_generation = 0

In [22]:
# pd.options.mode.chained_assignment = None 

df_generation = env_data[[0,1]]
df_generation.columns = ['Date','Generation']

In [23]:
df_generation['Date'] = pd.to_datetime(df_generation['Date'])

/tmp/ipykernel_55612/3725409118.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_generation['Date'] = pd.to_datetime(df_generation['Date'])


In [24]:
df_generation['Year'] = df_generation['Date'].apply(lambda time: time.year)
df_generation['Month'] = df_generation['Date'].apply(lambda time: time.month)
dmap = {1:'January',2:'February',3:'March',4:'April',5:'May',6:'June',7:'July',8:'August',9:'September',10:'October',11:'November',12:'December'}
df_generation['Month'] = df_generation['Month'].map(dmap)
df_generation['Day'] = df_generation['Date'].apply(lambda time: time.day)
df_generation['Day of Week'] = df_generation['Date'].apply(lambda time: time.dayofweek)
dmap1 = {0:'Mon',1:'Tue',2:'Wed',3:'Thu',4:'Fri',5:'Sat',6:'Sun'}
df_generation['Day of Week'] = df_generation['Day of Week'].map(dmap1)
df_generation['Hour'] = df_generation['Date'].apply(lambda time: time.hour)
df_generation['Minutes'] = df_generation['Date'].apply(lambda time: time.minute)

/tmp/ipykernel_55612/406952806.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_generation['Year'] = df_generation['Date'].apply(lambda time: time.year)
/tmp/ipykernel_55612/406952806.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_generation['Month'] = df_generation['Date'].apply(lambda time: time.month)
/tmp/ipykernel_55612/406952806.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See th

In [25]:
df_generation

Date  Generation  Year    Month  Day Day of Week  Hour  \
0    2017-01-01 00:00:00         0.0  2017  January    1         Sun     0   
1    2017-01-01 00:30:00        -0.0  2017  January    1         Sun     0   
2    2017-01-01 01:00:00        -0.0  2017  January    1         Sun     1   
3    2017-01-01 01:30:00        -0.0  2017  January    1         Sun     1   
4    2017-01-01 02:00:00        -0.0  2017  January    1         Sun     2   
...                  ...         ...   ...      ...  ...         ...   ...   
8683 2017-06-30 21:30:00        -0.0  2017     June   30         Fri    21   
8684 2017-06-30 22:00:00        -0.0  2017     June   30         Fri    22   
8685 2017-06-30 22:30:00        -0.0  2017     June   30         Fri    22   
8686 2017-06-30 23:00:00        -0.0  2017     June   30         Fri    23   
8687 2017-06-30 23:30:00        -0.0  2017     June   30         Fri    23   

      Minutes  
0           0  
1          30  
2           0  
3          30  
4           0  
...       ...  
8683       30  
8684        0  
8685       30  
8686        0  
8687       30  

[8688 rows x 8 columns]

In [26]:
df_generation[df_generation['Generation']==1.764]['Hour'].value_counts()
# Determining the hours at which the generation is the biggest

12    61
13    36
11     8
Name: Hour, dtype: int64

In [27]:
df_generation[df_generation['Generation']==1.764]['Month'].value_counts()
# Determining the months at which the generation is the biggest

April       48
March       42
May         12
February     3
Name: Month, dtype: int64

In [28]:
df_generation[df_generation['Generation']==0]['Hour'].value_counts()
# Determining the hours at which the generation is non existential

0     362
1     362
2     362
3     362
4     362
20    362
21    362
22    362
23    362
5     252
19    236
6     164
18    110
7      72
17     15
Name: Hour, dtype: int64

# Stable Baselines ALGORITHMS

Uncomment the algorithm

In [ ]:
##DQN
## parameters
gamma=0.99
learning_rate=1e-3
buffer_size=1e6

exploration_fraction=0.01
exploration_final_eps=0.02 
exploration_initial_eps=1.0
train_freq=1
batch_size=32
double_q=True
learning_starts=1000
target_network_update_freq=500

prioritized_replay=False
prioritized_replay_alpha=0.6
prioritized_replay_beta0=0.4
prioritized_replay_beta_iters=None
prioritized_replay_eps=1e-06
param_noise=True
n_cpu_tf_sess=None
verbose=0 
tensorboard_log=None
_init_setup_model=True
policy_kwargs=None
full_tensorboard_log=False
seed=None
# Policy='LnMlpPolicy'

## Train model
model = DQN('MlpPolicy', env, learning_rate=learning_rate, verbose=1,batch_size=batch_size,exploration_fraction=exploration_fraction,)
model.learn(total_timesteps=int(5e6))

##Proximal Policy Optimization
# model = PPO("MlpPolicy", env, verbose=1)
# model.learn(total_timesteps=4e5)


## Other algorithms
#SAC
# model = SAC('MlpPolicy', env, verbose=2).learn(total_timesteps=1e5)

#A2C
# model = A2C(MlpPolicy, env, verbose=1)
# model.learn(total_timesteps=25000)

/home/acr/anaconda3/lib/python3.9/site-packages/torch/cuda/__init__.py:80: UserWarning: CUDA initialization: CUDA unknown error - this may be due to an incorrectly set up environment, e.g. changing env variable CUDA_VISIBLE_DEVICES after program start. Setting the available devices to be zero. (Triggered internally at  ../c10/cuda/CUDAFunctions.cpp:112.)
  return torch._C._cuda_getDeviceCount() > 0


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-138968.0
-122056.5
-110206.5
-119719.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.23e+05 |
|    exploration_rate | 0.996     |
| time/               |           |
|    episodes         | 4         |
|    fps              | 4409      |
|    time_elapsed     | 0         |
|    total_timesteps  | 188       |
-----------------------------------
-103370.0
-121687.0
-120384.0
-76597.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.14e+05 |
|    exploration_rate | 0.993     |
| time/               |           |
|    episodes         | 8         |
|    fps              | 4728      |
|    time_elapsed     | 0         |
|    total_timesteps  | 376       |
-----------------------------------
-129500.5
-104007.0
-115945.0
-1141

-112509.0
-117512.5
-103958.0
-118563.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.16e+05 |
|    exploration_rate | 0.929     |
| time/               |           |
|    episodes         | 80        |
|    fps              | 5530      |
|    time_elapsed     | 0         |
|    total_timesteps  | 3760      |
-----------------------------------
-100917.5
-118934.0
-110976.0
-103847.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.16e+05 |
|    exploration_rate | 0.925     |
| time/               |           |
|    episodes         | 84        |
|    fps              | 5550      |
|    time_elapsed     | 0         |
|    total_timesteps  | 3948      |
-----------------------------------
-113673.0
-114600
-117410.0
-118041.0
-----------------------------------
| rollout/            |           |
|    ep_len_mean  

-122715.5
-103650.0
-109255.5
-110704.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.15e+05 |
|    exploration_rate | 0.861     |
| time/               |           |
|    episodes         | 156       |
|    fps              | 5218      |
|    time_elapsed     | 1         |
|    total_timesteps  | 7332      |
-----------------------------------
-120302.0
-108193.0
-119547.5
-114141.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.14e+05 |
|    exploration_rate | 0.857     |
| time/               |           |
|    episodes         | 160       |
|    fps              | 5216      |
|    time_elapsed     | 1         |
|    total_timesteps  | 7520      |
-----------------------------------
-119036.5
-121786.0
-125574.5
-116186.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean

-115303.0
-114670.5
-125923.0
-108065.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.15e+05 |
|    exploration_rate | 0.793     |
| time/               |           |
|    episodes         | 232       |
|    fps              | 5290      |
|    time_elapsed     | 2         |
|    total_timesteps  | 10904     |
-----------------------------------
-106555.0
-113103.0
-112947.0
-109589.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.15e+05 |
|    exploration_rate | 0.789     |
| time/               |           |
|    episodes         | 236       |
|    fps              | 5297      |
|    time_elapsed     | 2         |
|    total_timesteps  | 11092     |
-----------------------------------
-122444.0
-121765.5
-122031.5
-124369.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean

...

-11920.5
-38497.5
8091.5
-9477.0
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -2.69e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24392     |
|    fps              | 747       |
|    time_elapsed     | 1533      |
|    total_timesteps  | 1146424   |
| train/              |           |
|    learning_rate    | 0.001     |
|    loss             | 1.35e+03  |
|    n_updates        | 274105    |
-----------------------------------
-51366.0
-1520.4999999999973
8192.0
-8353.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -2.52e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24396     |
|    fps              | 747       |
|    time_elapsed     | 1533      |
|    total_timesteps  | 1146612   |
| train/              |

-1354.5
-33303.0
159.0
5288.0
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -2.05e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24452     |
|    fps              | 747       |
|    time_elapsed     | 1537      |
|    total_timesteps  | 1149244   |
| train/              |           |
|    learning_rate    | 0.001     |
|    loss             | 898       |
|    n_updates        | 274810    |
-----------------------------------
-33169.5
462.0
13800
13800
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -2.06e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24456     |
|    fps              | 747       |
|    time_elapsed     | 1537      |
|    total_timesteps  | 1149432   |
| train/              |           |
|    le

-56795.5
-68799.5
4525.0
13800
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 47       |
|    ep_rew_mean      | -1.5e+04 |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 24512    |
|    fps              | 747      |
|    time_elapsed     | 1541     |
|    total_timesteps  | 1152064  |
| train/              |          |
|    learning_rate    | 0.001    |
|    loss             | 3.12e+03 |
|    n_updates        | 275515   |
----------------------------------
-9424.0
13800
-3700.0
-636.9999999999986
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.39e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24516     |
|    fps              | 747       |
|    time_elapsed     | 1541      |
|    total_timesteps  | 1152252   |
| train/              |           |
|    le

13800
-8830.5
-5693.0
-8907.499999999998
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.51e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24572     |
|    fps              | 747       |
|    time_elapsed     | 1545      |
|    total_timesteps  | 1154884   |
| train/              |           |
|    learning_rate    | 0.001     |
|    loss             | 1.88e+03  |
|    n_updates        | 276220    |
-----------------------------------
13800
-54306.5
4862.5
-420.00000000000045
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.48e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24576     |
|    fps              | 747       |
|    time_elapsed     | 1545      |
|    total_timesteps  | 1155072   |
| train/         

-8700.0
7622.0
3812.5
-9424.0
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.16e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24632     |
|    fps              | 747       |
|    time_elapsed     | 1549      |
|    total_timesteps  | 1157704   |
| train/              |           |
|    learning_rate    | 0.001     |
|    loss             | 4.65e+03  |
|    n_updates        | 276925    |
-----------------------------------
7166.0
-1875.9999999999982
4048.5
2696.5
-----------------------------------
| rollout/            |           |
|    ep_len_mean      | 47        |
|    ep_rew_mean      | -1.09e+04 |
|    exploration_rate | 0.05      |
| time/               |           |
|    episodes         | 24636     |
|    fps              | 747       |
|    time_elapsed     | 1549      |
|    total_timesteps  | 1157892   |
| train/              |      

# Load a trained model 
(saved model files must be in .zip )


In [ ]:
#Load + Save Model
# Save model
# model.save('ppo_1day')

#Load Model
# filename='DQN_1day_6.7e5steps_2hours'
# filename = 'DQN_1day_100000_steps'
# model_trained = DQN.load(filename, env=env) 

# filename='ppo_1day_5e6steps_7910seconds' # Na verdade bastam bastante menos steps mas este dá sempre 10 de reward
# model_trained = PPO.load(filename, env=env) #

# filename='A2C_1day_6e5_steps_1088seconds'
# model_trained = A2C.load(filename, env=env) #

# model_trained = DQN.load('flexenv_dqn', env=env)

# model=model_trained

# Evaluate the agent

In [ ]:
mean_reward, std_reward = evaluate_policy(model,env, n_eval_episodes=5)

## Enjoy trained agent
action_track=[]
state_track=[]
obs = env.reset()

for i in range(timesteps):
    action, _states = model.predict(obs, deterministic=True)
    action_track.append(action)
    state_track.append(obs)
    obs, rewards, dones, info = env.step(action)
    
    env.render()

state_track=np.array(state_track)

#translate actions into charging power
action_track=[env.get_load(k) for k in action_track]

# Modificação António do Evaluate Agent

In [ ]:
## Enjoy trained agent
action_track=[]
state_track=[]
obs = env.reset()

for i in range(timesteps):
    action, states = model.predict(obs)
    print(obs)
    print(action)
    print('')
#     print(states)
    action_track.append(int(action))
    state_track.append(obs)
    obs, rewards, done, info = env.step(action)
    
    env.render()

state_track=np.array(state_track)

#translate actions into charging power
action_numbers = action_track
action_track=[env.get_load(k) for k in action_track]

In [ ]:
action_numbers

In [ ]:
action_track

In [ ]:
# State definition
        # 0-->t : time slot
        # 1-->gen : PV generation at timeslot t
        # 2-->load : Load at timeslot t
        # 3--> SOC : State of charge
        # 4-->SOC_1 : State of charge t-1
        # 5-->tar : Electricity tariff at timeslot t
        # 6-->R  : total reward per episode
        # 7 --> sc: self-consumption
        # 8 --> r :reward

# Plots

In [ ]:
flex.makeplot(48,state_track[:,3],action_track,env.data[:,0],env.data[:,1],env) # O Tempo e o Env não estão a fazer nada
# makeplot(T,soc,sol,gen,load,env): Tempo, SOC, Bat_Charge, Generation, load, env

In [ ]:
flex.reward_plot(env.R_Total)

In [ ]:
evaluate_policy(model,env, n_eval_episodes=10)

# Studying the battery

In [ ]:
SOC = state_track[:,3]
bat_charge = action_track # Bat_charge
gen = env.data[:,0]
load = env.data[:,1]

In [ ]:
state_track

In [ ]:
def myplot(x):
    plt.figure(figsize=(10,6))
    plt.plot(x)

In [ ]:
env.data

In [ ]:
myplot(gen)

In [ ]:
gen

In [ ]:
myplot(load)

In [ ]:
myplot(SOC)

In [ ]:
myplot(bat_charge)

In [ ]:
plt.figure(figsize=(10,7))
plt.legend
plt.plot(bat_charge,label='bat_charge')
plt.plot(gen,label='gen')
plt.legend()
plt.show()

In [ ]:
eta = 0.95
dh=30*(1/60)

In [ ]:
SOC

In [ ]:
gen

In [ ]:
C=np.array(bat_charge)*eta*dh
Sum=[]
Sumi = 0
for i in range(len(np.array(bat_charge)*eta*dh)):
    Sumi+= C[i]
    Sum.append(Sumi)
Sum

In [ ]:
SOC

In [ ]:
# bat_charge

In [ ]:
# self.charge_lim=3
charge_lim=3

charge_steps=np.linspace(0,charge_lim,int((charge_lim/0.2)+1))
charge_steps